# Data Cleanup

In [241]:
# Read the data from the csv
import pandas as pd

path = r'/Users/rajharsora/Library/CloudStorage/Box-Box/Oldenburg-Shared/Raj/Behavioral Box Testing/H1.1/4.20.2023 (Constant Water)/4_20_23_H1.1_Coordinates Log 1.2023_Day2'

df = pd.read_csv(path, delimiter='\t', header=None)
df

0                1
0         10:23:58.679  Arduino Logging
1      x = 127 y = 134              NaN
2         10:23:58.679              NaN
3      x = 127 y = 134              NaN
4         10:23:58.692              NaN
...                ...              ...
32059  x = 125 y = 133              NaN
32060     10:28:59.128              NaN
32061  x = 126 y = 133              NaN
32062     10:29:02.205              NaN
32063                x              NaN

[32064 rows x 2 columns]

In [242]:
#Seperate columns based on Timestamp or Coordinate value into separate dataframes

Timestamps_df = df.iloc[::2]
Coordinates_df = df.iloc[1::2]

#Reset the index of both dataframes
Timestamps_df = Timestamps_df.reset_index(drop=True)
Coordinates_df = Coordinates_df.reset_index(drop=True)

In [243]:
Coordinates_df

0    1
0      x = 127 y = 134  NaN
1      x = 127 y = 134  NaN
2      x = 127 y = 134  NaN
3      x = 127 y = 135  NaN
4      x = 127 y = 134  NaN
...                ...  ...
16027  x = 126 y = 133  NaN
16028  x = 125 y = 133  NaN
16029  x = 125 y = 133  NaN
16030  x = 126 y = 133  NaN
16031                x  NaN

[16032 rows x 2 columns]

## Cleaning up the Coordinates Dataframe

In [244]:
#Drop Column 1 from the dataframe (just filled with NaN values
Coordinates_df.drop(1, axis=1, inplace=True)

In [245]:
Coordinates_df

0
0      x = 127 y = 134
1      x = 127 y = 134
2      x = 127 y = 134
3      x = 127 y = 135
4      x = 127 y = 134
...                ...
16027  x = 126 y = 133
16028  x = 125 y = 133
16029  x = 125 y = 133
16030  x = 126 y = 133
16031                x

[16032 rows x 1 columns]

In [246]:
#Seperate X and Y coordinates into two different columns

Coordinates_df[['X Coordinate', 'Y Coordinate']] = Coordinates_df[0].str.extract(r'^(x = \d+)\s(.*)$')

#Drop any null values in the dataframe
Coordinates_df.dropna(inplace=True)

#Get it so there are only integers in the X Coordinate and Y Coordinate Column
Coordinates_df['X Coordinate'] = Coordinates_df['X Coordinate'].str.replace('x = ', '').astype(int)

Coordinates_df['Y Coordinate'] = Coordinates_df['Y Coordinate'].str.replace('y = ', '').astype(int)

# Rename Column 0
Coordinates_df = Coordinates_df.rename(columns = {0: 'Raw Data'})

In [247]:
Coordinates_df

Raw Data  X Coordinate  Y Coordinate
0      x = 127 y = 134           127           134
1      x = 127 y = 134           127           134
2      x = 127 y = 134           127           134
3      x = 127 y = 135           127           135
4      x = 127 y = 134           127           134
...                ...           ...           ...
16026  x = 125 y = 133           125           133
16027  x = 126 y = 133           126           133
16028  x = 125 y = 133           125           133
16029  x = 125 y = 133           125           133
16030  x = 126 y = 133           126           133

[16031 rows x 3 columns]

## Cleaning up the Timestamps dataframe

In [248]:
Timestamps_df

0                1
0      10:23:58.679  Arduino Logging
1      10:23:58.679              NaN
2      10:23:58.692              NaN
3      10:23:58.738              NaN
4      10:23:58.738              NaN
...             ...              ...
16027  10:28:58.870              NaN
16028  10:28:58.888              NaN
16029  10:28:58.907              NaN
16030  10:28:59.128              NaN
16031  10:29:02.205              NaN

[16032 rows x 2 columns]

In [249]:
#Drop Column 1
Timestamps_df.drop(1, axis=1, inplace=True)

#Rename Column 0
Timestamps_df = Timestamps_df.rename(columns = {0: 'Timestamp'})

## Combining Cleaned Dataframe

In [250]:
df_merged = pd.concat([Timestamps_df['Timestamp'], Coordinates_df['Raw Data'], Coordinates_df['X Coordinate'], Coordinates_df['Y Coordinate']], axis=1)

In [251]:
df_merged

Timestamp         Raw Data  X Coordinate  Y Coordinate
0      10:23:58.679  x = 127 y = 134         127.0         134.0
1      10:23:58.679  x = 127 y = 134         127.0         134.0
2      10:23:58.692  x = 127 y = 134         127.0         134.0
3      10:23:58.738  x = 127 y = 135         127.0         135.0
4      10:23:58.738  x = 127 y = 134         127.0         134.0
...             ...              ...           ...           ...
16027  10:28:58.870  x = 126 y = 133         126.0         133.0
16028  10:28:58.888  x = 125 y = 133         125.0         133.0
16029  10:28:58.907  x = 125 y = 133         125.0         133.0
16030  10:28:59.128  x = 126 y = 133         126.0         133.0
16031  10:29:02.205              NaN           NaN           NaN

[16032 rows x 4 columns]

In [252]:
#Drop any duplicate rows by looking at the 'Timestamp' column
df_merged = df_merged.drop_duplicates(subset=['Timestamp'])

In [253]:
#Reset the index
df_merged = df_merged.reset_index(drop=True)

In [254]:
#Convert the 'Timestamp' column to datetime format from strings

df_merged['Timestamp'] = pd.to_datetime(df_merged['Timestamp'])

#Make a column for change in time from the start of the trial
df_merged['Time_delta(ms)'] = df_merged['Timestamp'] - df_merged['Timestamp'].iloc[0]

#Make the Time_delta column easier to read by only showing ms
df_merged['Time_delta(ms)'] = df_merged['Time_delta(ms)'].apply(lambda x: int(x.total_seconds() * 1000)).astype(int)

In [255]:
df_merged

Timestamp         Raw Data  X Coordinate  Y Coordinate  \
0     2023-05-07 10:23:58.679  x = 127 y = 134         127.0         134.0   
1     2023-05-07 10:23:58.692  x = 127 y = 134         127.0         134.0   
2     2023-05-07 10:23:58.738  x = 127 y = 135         127.0         135.0   
3     2023-05-07 10:23:58.753  x = 128 y = 135         128.0         135.0   
4     2023-05-07 10:23:58.790  x = 127 y = 134         127.0         134.0   
...                       ...              ...           ...           ...   
13781 2023-05-07 10:28:58.870  x = 126 y = 133         126.0         133.0   
13782 2023-05-07 10:28:58.888  x = 125 y = 133         125.0         133.0   
13783 2023-05-07 10:28:58.907  x = 125 y = 133         125.0         133.0   
13784 2023-05-07 10:28:59.128  x = 126 y = 133         126.0         133.0   
13785 2023-05-07 10:29:02.205              NaN           NaN           NaN   

       Time_delta(ms)  
0                   0  
1                  13  
2                  59  
3                  74  
4                 111  
...               ...  
13781          300191  
13782          300209  
13783          300228  
13784          300449  
13785          303526  

[13786 rows x 5 columns]

# Analysis

## Configuration for Graphs

In [256]:
#Put the bounds for what is considered to be a push or a pull here

push = 130
pull = 123

## Coordinates vs Time (Line Plot)

In [257]:
import plotly.graph_objs as go

#Create figure
fig1 = go.Figure()

#Create Figure
fig1.add_trace(
    go.Scatter(x = df_merged['Time_delta(ms)'], y = df_merged['X Coordinate'], mode = 'lines', line = dict(color='#58508d'), name = 'X Coorindate')
)

fig1.add_trace(
	go.Scatter(x = df_merged['Time_delta(ms)'], y = df_merged['Y Coordinate'], mode = 'lines', line = dict(color='#ff6361'), name = 'Y Coordinate')
)

#Add bounds
fig1.add_shape(type="line", x0=df_merged['Time_delta(ms)'].min(), y0=130, x1=df_merged['Time_delta(ms)'].max(), y1=push, line=dict(color="orange", width=2), name = 'Push Bound')
fig1.add_shape(type="line", x0=df_merged['Time_delta(ms)'].min(), y0=123, x1=df_merged['Time_delta(ms)'].max(), y1=pull, line=dict(color="orange", width=2), name = 'Pull Bound')

#Zoom functionality
fig1.update_layout(
	title="Time Elapsed vs X Coorindate",
	xaxis=dict(
		title="Time Elapsed (ms)",
		showgrid=True,
		zeroline=False,
		showline=True
	),
	yaxis=dict(
		title="X Coordinate",
		showgrid=True,
		zeroline=False,
		showline=True
	),
	dragmode='pan',
	hovermode='x',
	hoverdistance=100,
	spikedistance=1000
)


fig1.show()

## Coordinates vs Time 3D Line Plot

In [258]:
import plotly.express as px

fig2 = px.line_3d(df_merged, x = df_merged['X Coordinate'], y = df_merged['Y Coordinate'], z = df_merged['Time_delta(ms)'])

fig2.show()

In [260]:
# Read the data from the csv
import pandas as pd

path = r'/Users/rajharsora/Library/CloudStorage/Box-Box/Oldenburg-Shared/Raj/Behavioral Box Testing/H1.1/4.20.2023 (Constant Water)/4_20_23_H1.1_Coordinates Log 1.2023_Day2'

df = pd.read_csv(path, delimiter='\t', header=None)
df

0                1
0         10:23:58.679  Arduino Logging
1      x = 127 y = 134              NaN
2         10:23:58.679              NaN
3      x = 127 y = 134              NaN
4         10:23:58.692              NaN
...                ...              ...
32059  x = 125 y = 133              NaN
32060     10:28:59.128              NaN
32061  x = 126 y = 133              NaN
32062     10:29:02.205              NaN
32063                x              NaN

[32064 rows x 2 columns]

In [261]:
#Seperate columns based on Timestamp or Coordinate value into separate dataframes

Timestamps_df = df.iloc[::2]
Coordinates_df = df.iloc[1::2]

#Reset the index of both dataframes
Timestamps_df = Timestamps_df.reset_index(drop=True)
Coordinates_df = Coordinates_df.reset_index(drop=True)

In [262]:
Coordinates_df

0    1
0      x = 127 y = 134  NaN
1      x = 127 y = 134  NaN
2      x = 127 y = 134  NaN
3      x = 127 y = 135  NaN
4      x = 127 y = 134  NaN
...                ...  ...
16027  x = 126 y = 133  NaN
16028  x = 125 y = 133  NaN
16029  x = 125 y = 133  NaN
16030  x = 126 y = 133  NaN
16031                x  NaN

[16032 rows x 2 columns]

## Cleaning up the Coordinates Dataframe

In [263]:
#Drop Column 1 from the dataframe (just filled with NaN values
Coordinates_df.drop(1, axis=1, inplace=True)

In [264]:
Coordinates_df

0
0      x = 127 y = 134
1      x = 127 y = 134
2      x = 127 y = 134
3      x = 127 y = 135
4      x = 127 y = 134
...                ...
16027  x = 126 y = 133
16028  x = 125 y = 133
16029  x = 125 y = 133
16030  x = 126 y = 133
16031                x

[16032 rows x 1 columns]

In [265]:
#Seperate X and Y coordinates into two different columns

Coordinates_df[['X Coordinate', 'Y Coordinate']] = Coordinates_df[0].str.extract(r'^(x = \d+)\s(.*)$')

#Drop any null values in the dataframe
Coordinates_df.dropna(inplace=True)

#Get it so there are only integers in the X Coordinate and Y Coordinate Column

Coordinates_df['X Coordinate'] = Coordinates_df['X Coordinate'].str.replace('x = ', '').astype(int)

Coordinates_df['Y Coordinate'] = Coordinates_df['Y Coordinate'].str.replace('y = ', '').astype(int)

# Rename Column 0
Coordinates_df = Coordinates_df.rename(columns = {0: 'Raw Data'})

In [266]:
Coordinates_df

Raw Data  X Coordinate  Y Coordinate
0      x = 127 y = 134           127           134
1      x = 127 y = 134           127           134
2      x = 127 y = 134           127           134
3      x = 127 y = 135           127           135
4      x = 127 y = 134           127           134
...                ...           ...           ...
16026  x = 125 y = 133           125           133
16027  x = 126 y = 133           126           133
16028  x = 125 y = 133           125           133
16029  x = 125 y = 133           125           133
16030  x = 126 y = 133           126           133

[16031 rows x 3 columns]

## Cleaning up the Timestamps dataframe

In [267]:
Timestamps_df

0                1
0      10:23:58.679  Arduino Logging
1      10:23:58.679              NaN
2      10:23:58.692              NaN
3      10:23:58.738              NaN
4      10:23:58.738              NaN
...             ...              ...
16027  10:28:58.870              NaN
16028  10:28:58.888              NaN
16029  10:28:58.907              NaN
16030  10:28:59.128              NaN
16031  10:29:02.205              NaN

[16032 rows x 2 columns]

In [268]:
#Drop Column 1
Timestamps_df.drop(1, axis=1, inplace=True)

#Rename Column 0
Timestamps_df = Timestamps_df.rename(columns = {0: 'Timestamp'})

## Combining Cleaned Dataframe

In [269]:
df_merged = pd.concat([Timestamps_df['Timestamp'], Coordinates_df['Raw Data'], Coordinates_df['X Coordinate'], Coordinates_df['Y Coordinate']], axis=1)

In [270]:
df_merged

Timestamp         Raw Data  X Coordinate  Y Coordinate
0      10:23:58.679  x = 127 y = 134         127.0         134.0
1      10:23:58.679  x = 127 y = 134         127.0         134.0
2      10:23:58.692  x = 127 y = 134         127.0         134.0
3      10:23:58.738  x = 127 y = 135         127.0         135.0
4      10:23:58.738  x = 127 y = 134         127.0         134.0
...             ...              ...           ...           ...
16027  10:28:58.870  x = 126 y = 133         126.0         133.0
16028  10:28:58.888  x = 125 y = 133         125.0         133.0
16029  10:28:58.907  x = 125 y = 133         125.0         133.0
16030  10:28:59.128  x = 126 y = 133         126.0         133.0
16031  10:29:02.205              NaN           NaN           NaN

[16032 rows x 4 columns]

In [271]:
#Drop any duplicate rows by looking at the 'Timestamp' column
df_merged = df_merged.drop_duplicates(subset=['Timestamp'])

In [272]:
#Reset the index
df_merged = df_merged.reset_index(drop=True)

In [273]:
#Convert the 'Timestamp' column to datetime format from strings

df_merged['Timestamp'] = pd.to_datetime(df_merged['Timestamp'])

#Make a column for change in time from the start of the trial
df_merged['Time_delta(ms)'] = df_merged['Timestamp'] - df_merged['Timestamp'].iloc[0]

#Make the Time_delta column easier to read by only showing ms
df_merged['Time_delta(ms)'] = df_merged['Time_delta(ms)'].apply(lambda x: int(x.total_seconds() * 1000)).astype(int)

In [274]:
df_merged

Timestamp         Raw Data  X Coordinate  Y Coordinate  \
0     2023-05-07 10:23:58.679  x = 127 y = 134         127.0         134.0   
1     2023-05-07 10:23:58.692  x = 127 y = 134         127.0         134.0   
2     2023-05-07 10:23:58.738  x = 127 y = 135         127.0         135.0   
3     2023-05-07 10:23:58.753  x = 128 y = 135         128.0         135.0   
4     2023-05-07 10:23:58.790  x = 127 y = 134         127.0         134.0   
...                       ...              ...           ...           ...   
13781 2023-05-07 10:28:58.870  x = 126 y = 133         126.0         133.0   
13782 2023-05-07 10:28:58.888  x = 125 y = 133         125.0         133.0   
13783 2023-05-07 10:28:58.907  x = 125 y = 133         125.0         133.0   
13784 2023-05-07 10:28:59.128  x = 126 y = 133         126.0         133.0   
13785 2023-05-07 10:29:02.205              NaN           NaN           NaN   

       Time_delta(ms)  
0                   0  
1                  13  
2                  59  
3                  74  
4                 111  
...               ...  
13781          300191  
13782          300209  
13783          300228  
13784          300449  
13785          303526  

[13786 rows x 5 columns]

# Analysis

## Configuration for Graphs

In [275]:
#Put the bounds for what is considered to be a push or a pull here

push = 130
pull = 123

## Coordinates vs Time (Line Plot)

In [276]:
import plotly.graph_objs as go

#Create figure
fig1 = go.Figure()

#Create Figure
fig1.add_trace(
    go.Scatter(x = df_merged['Time_delta(ms)'], y = df_merged['X Coordinate'], mode = 'lines', line = dict(color='#58508d'), name = 'X Coorindate')
)

fig1.add_trace(
	go.Scatter(x = df_merged['Time_delta(ms)'], y = df_merged['Y Coordinate'], mode = 'lines', line = dict(color='#ff6361'), name = 'Y Coordinate')
)

#Add bounds
fig1.add_shape(type="line", x0=df_merged['Time_delta(ms)'].min(), y0=130, x1=df_merged['Time_delta(ms)'].max(), y1=push, line=dict(color="orange", width=2), name = 'Push Bound')
fig1.add_shape(type="line", x0=df_merged['Time_delta(ms)'].min(), y0=123, x1=df_merged['Time_delta(ms)'].max(), y1=pull, line=dict(color="orange", width=2), name = 'Pull Bound')

#Zoom functionality
fig1.update_layout(
	title="Time Elapsed vs X Coorindate",
	xaxis=dict(
		title="Time Elapsed (ms)",
		showgrid=True,
		zeroline=False,
		showline=True
	),
	yaxis=dict(
		title="X Coordinate",
		showgrid=True,
		zeroline=False,
		showline=True
	),
	dragmode='pan',
	hovermode='x',
	hoverdistance=100,
	spikedistance=1000
)


fig1.show()

## Coordinates vs Time 3D Line Plot

In [277]:
import plotly.express as px

fig2 = px.line_3d(df_merged, x = df_merged['X Coordinate'], y = df_merged['Y Coordinate'], z = df_merged['Time_delta(ms)'])

fig2.show()

# Drawnow

In [ ]:
import matplotlib.pyplot as plt
import matplotlib.animation as animation
import numpy as np

fig3, ax = plt.subplots()

line = ax.plot(df_merged['X Coordinate'], df_merged['Y Coordinate'])


def update(frame):
	# for each frame, update the data stored on each artist.
	x = df_merged['X Coordinate'][:frame]
	y = df_merged['Y Coordinate'][:frame]
	# update the line plot:
	line.set_xdata(df_merged['X Coordinate'][:frame])
	line.set_ydata(df_merged['Y Coordinate'][:frame])
	return (line)


ani = animation.FuncAnimation(fig=fig3, func=update, frames=1000, interval=100)
plt.show()


In [292]:
#TODO Figure out this Drawnow thing